In [11]:
import xml.etree.cElementTree as ET
import pprint
from collections import defaultdict
import re


f = 'osm_paris_central_sm.xml'
path = 'Documents/ds_nanodegree/data_wrangling/'
filename = path + f

In [5]:
#check for valid phone number format, eg: "+33 1 45 08 07 41"

test ="+33 7 27 11 45 63"
    
#invalid_phone(n)      

In [7]:
#the issues with phone numbers
'''
missing "+33 ", includes leading 0
missing "+33 ", includes leading 0, no spaces

no spaces
starts with "+331" or "+339"
space after 33 but nowhere else
space after 33 but nowhere else AND incl leading 0
no space after 33 and after city code
period separator instead of " " & leading 0
not a phone number
4-digit number 3631 (mairie?)'''


import re
valid_phone = re.compile(r'^\+33\s[1-9]\s\d{2}\s\d{2}\s\d{2}\s\d{2}$')

def invalid_phone(n):
    p = valid_phone.search(n)
    if p:
        pass
    else:
        return n

def reformat(n):
    cc = "+33 " 
    
    #remove spaces & periods
    n = n.replace(' ', '').replace('.', '')
    
    #if phone number is 9 char or longer, apply ITU-T E.123 standard
    if len(n) >= 9:
        n = cc + n[-9] + " " + n[-8:-6] + " " + n[-6:-4] + " " + n[-4:-2] + " " + n[-2:]
    else:
        pass
    return n


def fix_phone(n):
    if n.startswith("+33"):
        n = n[3:]
        n = reformat(n)
    elif n.startswith("0"):
        n = reformat(n)
    else:
        pass
    return n

def clean_phone(n):
    if invalid_phone(n):
        clean = fix_phone(n)
        return clean
    else:
        pass

#n = "00178186645"
#clean_phone(n)



In [10]:
import pprint

def audit_phone(filename):
    # YOUR CODE HERE
    #create empty dict
    invalid = {}
    total_phone = 0
    bad_phone = 0
    #find  tag
    for event, elem in ET.iterparse(filename):
        if elem.tag == "node":
            for child in elem:
                k,v = child.attrib['k'],child.attrib['v']
                if k == "name":
                    name = v
                if k =="phone":
                    total_phone +=1
                    if invalid_phone(v):
                        invalid[name] = clean_phone(v)
                        #invalid[name] = v
                    
                else:
                    pass
        else:
            pass
    return invalid

pprint.pprint(audit_phone(filename))


{u'11\xe8me Art': '+33 1 43 79 81 69',
 u'A premi\xe8re vue': '+33 1 43 57 74 66',
 'APEF': '+33 1 58 51 46 50',
 'ASVS Alarme Auto-surveillance': '+33 1 40 01 04 50',
 u'Acad\xe9mie Hotel': '+33 1 45 49 80 00',
 'Allo Sushi': '+33 1 44 61 93 73',
 'Amareto': '+33 1 46 28 07 07',
 'Arnaout': '+33 1 43 43 14 61',
 'Artmedium Cours de Dessin': '+33 6 69 00 48 20',
 'Atelier 3': '+33 6 99 76 40 00',
 'Atelier de Paris': '+33 1 44 73 83 50',
 'Atlassib': '+33 1 44 74 64 01',
 'Au 105': '+33 1 43 45 36 25',
 'Au Bouquet Saint-Paul': '+33 1 42 78 55 03',
 "Au P'tit Cahoua": '+33 1 47 00 20 42',
 u'Au Petit Tha\xef': '+33 1 42 72 75 75',
 u'Au Point V\xe9lo Hollandais': '+33 1 43 54 85 36',
 'Au Saint-Severin': '+33 1 43 54 19 36',
 'Au Trappiste': '+33 1 42 33 08 50',
 u'Au beurre sal\xe9': '+33 1 43 07 67 42',
 "Au lys d'argent": '+33 1 46 33 56 13',
 'Au royal mad': '+33 1 43 57 70 50',
 'Autour du Saumon': '+33 1 42 77 23 08',
 'Bai Thong': '+33 1 43 47 55 47',
 u"Bazar d'\xc9lectricit\xe

In [ ]:
def clean_phone2(filename):
    # YOUR CODE HERE
    #create empty dict
    invalid = {}
    for event, elem in ET.iterparse(filename):
        if elem.tag == "node":
            for child in elem:
                k,v = child.attrib['k'],child.attrib['v']
                if k =="phone":
                    if invalid_phone(v):
                        clean_v = fix_phone(v)
                        invalid[v] = clean_v     
                else:
                    pass
        else:
            pass
    return invalid

pprint.pprint(clean_phone2(filename))

In [8]:
lower = re.compile(r'^([a-z]|_)*$')
lower_colon = re.compile(r'^([a-z]|_)*:([a-z]|_)*$')
problemchars = re.compile(r'[=\+/&<>;\'"\?%#$@\,\. \t\r\n]')

CREATED = [ "version", "changeset", "timestamp", "user", "uid"]

def shape_element(element):
    node = {}
    created = {}
    address = {}
    pos = [0,0]
    node_refs = []
    
    if element.tag == "node" or element.tag == "way" :
        node["type"] = element.tag
        d = element.attrib
        
        for key, value in d.iteritems():
            
            #group creation metadata into a "created" sub-dict
            if key in CREATED:
                created[key] = value
                node["created"] = created
            
            #store lat & lon values in a list
            elif key == "lat":
                pos[0] = float(value)
                node["pos"] = pos
            elif key == "lon":
                pos[1] = float(value)
                node["pos"] = pos
            else:
                node[key] = value
        
        for child in element: 
            if child.tag == "tag":
                k,v = child.attrib["k"],child.attrib["v"]
                
                #skip tags with chars that may cause problems for mongo import
                p = problemchars.search(k)
                if p:
                    pass
                
                #process only address tags with one colon (in "addr:") 
                elif k.startswith("addr:") and k.find(":",5) ==-1:
                    address[k[5:]] = v
                    node["address"] = address
                
                #clean phone numbers
                elif k == "phone":
                    clean_ph = clean_phone(v)
                    node["phone"] = clean_ph
                
                #make all other key values dict keys
                elif not k.startswith("addr:"):
                    node[k] = child.attrib["v"]
                else:
                    pass
            
            #store nd tags in a list
            elif child.tag == "nd": 
                r = child.attrib["ref"]
                node_refs.append(r)
                node["node_refs"] = node_refs
        return node
    
    else:
        return None

In [ ]:
import codecs
import json

'''if you are using the process_map() procedure above on your own computer 
to write to a JSON file, make sure you call it with pretty = False parameter. 
Otherwise, mongoimport might give you an error when you try to import 
the JSON file to MongoDB.'''
    

def process_map(file_in, pretty = False):
    # You do not need to change this file
    file_out = "{0}.json".format(file_in)
    data = []
    with codecs.open(file_out, "w") as fo:
        for _, element in ET.iterparse(file_in):
            el = shape_element(element)
            if el:
                data.append(el)
                if pretty:
                    fo.write(json.dumps(el, indent=2)+"\n")
                else:
                    fo.write(json.dumps(el) + "\n")
    return data

#does this work?
pprint.pprint(process_map(filename, pretty = False))

[{'created': {'changeset': '32796508',
              'timestamp': '2015-07-22T09:09:14Z',
              'uid': '208829',
              'user': u'G\xe9ov\xe9lo',
              'version': '7'},
  'id': '361029',
  'pos': [48.8457578, 2.3674936],
  'type': 'node'},
 {'created': {'changeset': '4515716',
              'timestamp': '2010-04-24T20:33:32Z',
              'uid': '17286',
              'user': 'Pieren',
              'version': '10'},
  'highway': 'traffic_signals',
  'id': '361031',
  'pos': [48.8474791, 2.365556],
  'type': 'node'},
 {'created': {'changeset': '4514867',
              'timestamp': '2010-04-24T19:09:56Z',
              'uid': '17286',
              'user': 'Pieren',
              'version': '5'},
  'highway': 'traffic_signals',
  'id': '361032',
  'pos': [48.8508895, 2.3672954],
  'type': 'node'},
 {'created': {'changeset': '13141345',
              'timestamp': '2012-09-17T10:15:20Z',
              'uid': '456113',
              'user': 'eric_G',
              

In [14]:
#create sample
import xml.etree.ElementTree as ET  # Use cElementTree or lxml if too slow

# Replace this with your osm file - listed above already
SAMPLE_FILE = "Documents/ds_nanodegree/data_wrangling/sample.osm"


def get_element(filename, tags=('node', 'way', 'relation')):
    """Yield element if it is the right type of tag

    Reference:
    http://stackoverflow.com/questions/3095434/inserting-newlines-in-xml-file-generated-via-xml-etree-elementtree-in-python
    """
    context = ET.iterparse(filename, events=('start', 'end'))
    _, root = next(context)
    for event, elem in context:
        if event == 'end' and elem.tag in tags:
            yield elem
            root.clear()


with open(SAMPLE_FILE, 'wb') as output:
    output.write('<?xml version="1.0" encoding="UTF-8"?>\n')
    output.write('<osm>\n  ')

    # Write every 10th top level element
    for i, element in enumerate(get_element(filename)):
        if i % 10 == 0:
            output.write(ET.tostring(element, encoding='utf-8'))

    output.write('</osm>')